In [2]:
from nipype.interfaces.io import DataSink, SelectFiles, DataGrabber 
from nipype.interfaces.utility import IdentityInterface, Function    
from nipype.pipeline.engine import Node, Workflow, JoinNode, MapNode
from nipype.interfaces import fsl
from nipype.interfaces import brainsuite
from nipype.interfaces.io import SelectFiles, DataSink, DataGrabber
from shutil import copyfile
import pandas as pd
from glob import glob
from os.path import abspath, expanduser, join
from os import chdir, remove, getcwd
from nipype import config, logging
from datetime import date
today = str(date.today())
config.enable_debug_mode()

In [4]:
#Set variables
# subject_list = ['02-T2', '06-T1', '07-T2','08-T1', '09-T2', '10-T1', '11-T1', '12-T1', '13-T1', '15-T1', '16-T1', '17-T1',
#                 '18-T1', '19-T1', '20-T1', '21-T1', '22-T1', '23-T1', '24-T1', '29-T1', '30-T1', '31-T1', '32-T1',
#                 '35-T1', '36-T1', '37-T1', '38-T1', '40-T1', '102-T1', '103-T1', '104-T1', '105-T1', '106-T1', '107-T1', '108-T1', '109-T1',
#                 '110-T1', '111-T1']

#subject_list = ['08-T1']#, '20-T1','22-T1','29-T1','31-T1','35-T1']

home = '/Volumes/group/proc/TIGERanalysis'
fpath = join(home, 'qT1/subjDir')
workflow_dir = join(home, 'qT1/workflow')
data_dir = join(home, 'qT1/data')
data = '/Users/lucindasisk/Box/LS_Folders/TIGER_qT1_SOBP'

# subs = glob(data + '/*-*')
# subject_list = pd.Series(subs).str.replace(data + '/', '')
# subject_list

subs = pd.read_csv(home + '/scripts/qt1_sublist_02.08.20.txt', sep = ' ', header=None)
subject_list = subs[0].tolist()

#subject_list = ['097-T3']

In [6]:
#Setup Datasink, Infosource, Selectfiles

datasink = Node(DataSink(base_directory = data_dir),
                   name='datasink')

#Set infosource iterables
infosource = Node(IdentityInterface(fields=['subject_id']),
                  name="infosource")
infosource.iterables = [('subject_id', subject_list)]

#SelectFiles
template = dict(t1=fpath+'/{subject_id}/T1_acpc.nii.gz',
               qt1=data+'/{subject_id}/fw_qT1_t1fit_final.nii.gz')

sf = Node(SelectFiles(template, 
                      base_directory = fpath),
          name = 'sf')


In [7]:
#Skullstrip T1w image
stripT1 = Node(fsl.BET(out_file = 'T1_acpc_bet.nii.gz'),
             name = 'stripT1')

#Reorient qT1 to standard orientation
reorient = Node(fsl.Reorient2Std(out_file = 'reoriented_qT1.nii.gz',
                              output_type = 'NIFTI_GZ'),
                    name = 'reorient')

#Register qT1 to T1w
register_qt1 = Node(fsl.FLIRT(out_file = 'registered_qT1.nii.gz',
                              output_type = 'NIFTI_GZ',
                              out_matrix_file = 'flirt_transform_qt1.mat'),
                    name = 'register_qt1')

#Extract voxel values from qT1 beneath overlaid mask - Left Uncinate
get_voxLUF = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_LeftUncinate.txt'),
               name = 'get_voxLUF')

#Extract voxel values from qT1 beneath overlaid mask - Left Cingulum Cingulate
get_voxLCC = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_LeftCC.txt'),
               name = 'get_voxLCC')

#Extract voxel values from qT1 beneath overlaid mask - Right Uncinate
get_voxRUF = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_RightHipp.txt'),
               name = 'get_voxRUF')

#Extract voxel values from qT1 beneath overlaid mask - Right Cingulum Cingulate
get_voxRCC = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_LeftHipp.txt'),
               name = 'get_voxRCC')

200318-22:22:46,174 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:22:46,176 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:22:46,178 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:22:46,179 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:22:46,181 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:22:46,182 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:22:46,184 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [12]:
#Extract left hippocampus
extract_lhipp = Node(fsl.Threshold(thresh = 16.5, 
                                   direction = 'below', 
                                   args = '-uthr 17.5',
                                   output_type = 'NIFTI_GZ',
                                   out_file = 'left_hippocampus.nii.gz'),
                        name = 'extract_lhipp')
#Extract right hippocampus
extract_rhipp = Node(fsl.Threshold(thresh = 52.5, 
                                   direction = 'below', 
                                   args = '-uthr 53.5',
                                   output_type = 'NIFTI_GZ',
                                   out_file = 'right_hippocampus.nii.gz'),
                    name='extract_rhipp')

#Extract voxel values from qT1 beneath overlaid mask - Left Hippocampus
get_voxRhipp = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_RightHippocampus.txt'),
               name = 'get_voxRUF')

#Extract voxel values from qT1 beneath overlaid mask - Right Hippocampus
get_voxLhipp = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_RightCC.txt'),
               name = 'get_voxRCC')

200318-22:26:35,443 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:26:35,445 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:26:35,446 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI
200318-22:26:35,447 nipype.interface WARNING:
	 FSLOUTPUTTYPE environment variable is not set. Setting FSLOUTPUTTYPE=NIFTI


In [15]:
qt1proc_flow = Workflow(name='qt1proc_flow')
qt1proc_flow.connect([(infosource, sf, [('subject_id', 'subject_id')]),
                      (sf, stripT1, [('t1', 'in_file')]),
                      (stripT1, datasink, [('out_file', '1_check_alignment')]),
                      (sf, reorient, [('qt1', 'in_file')]),
                      (reorient, datasink, [
                       ('out_file', '1_check_alignment.@par')]),
                      (reorient, register_qt1, [('out_file', 'in_file')]),
                      (stripT1, register_qt1, [('out_file', 'reference')]),
                      (register_qt1, datasink, [
                       ('out_file', '1_check_alignment.@par.@par')])
                      ])

qt1proc_flow.base_dir = workflow_dir
qt1proc_flow.write_graph(graph2use='flat')
preproc = qt1proc_flow.run('MultiProc', plugin_args={'n_procs': 4})

200209-15:48:12,512 nipype.workflow DEBUG:
	 (qt1proc_flow.infosource, qt1proc_flow.sf): No edge data
200209-15:48:12,513 nipype.workflow DEBUG:
	 (qt1proc_flow.infosource, qt1proc_flow.sf): new edge data: {'connect': [('subject_id', 'subject_id')]}
200209-15:48:12,514 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.stripT1): No edge data
200209-15:48:12,515 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.stripT1): new edge data: {'connect': [('t1', 'in_file')]}
200209-15:48:12,515 nipype.workflow DEBUG:
	 (qt1proc_flow.stripT1, qt1proc_flow.datasink): No edge data
200209-15:48:12,516 nipype.workflow DEBUG:
	 (qt1proc_flow.stripT1, qt1proc_flow.datasink): new edge data: {'connect': [('out_file', '1_check_alignment')]}
200209-15:48:12,516 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.reorient): No edge data
200209-15:48:12,517 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.reorient): new edge data: {'connect': [('qt1', 'in_file')]}
200209-15:48:12,518 

	 Removing contents of /Volumes/group/proc/TIGERanalysis/qT1/workflow/qt1proc_flow/_subject_id_097-T3/register_qt1
200209-15:49:18,309 nipype.utils DEBUG:
	 Creating directory /Volumes/group/proc/TIGERanalysis/qT1/workflow/qt1proc_flow/_subject_id_097-T3/register_qt1
200209-15:49:19,114 nipype.workflow DEBUG:
	 Progress: 5 jobs, 3/1/0 (done/running/ready), 1/1 (pending_tasks/waiting).
200209-15:49:19,115 nipype.workflow DEBUG:
	 Tasks currently running: 1. Pending: 1.
200209-15:49:19,117 nipype.workflow INFO:
	 [MultiProc] Running 1 tasks, and 0 jobs ready. Free memory (GB): 28.60/28.80, Free processors: 3/4.
                     Currently running:
                       * qt1proc_flow.register_qt1
200209-15:49:19,711 nipype.utils DEBUG:
	 Creating directory /Volumes/group/proc/TIGERanalysis/qT1/workflow/qt1proc_flow/_subject_id_097-T3/register_qt1/_report
200209-15:49:21,631 nipype.workflow DEBUG:
	 [Node] Writing pre-exec report to "/Volumes/group/proc/TIGERanalysis/qT1/workflow/qt1p

200209-15:50:35,188 nipype.workflow DEBUG:
	 Checking hash "qt1proc_flow.datasink" locally: cached=False, updated=False.
200209-15:50:35,191 nipype.workflow DEBUG:
	 [MultiProc] Submitted task qt1proc_flow.datasink (taskid=3).
200209-15:50:35,194 nipype.workflow DEBUG:
	 Progress: 5 jobs, 4/1/0 (done/running/ready), 1/0 (pending_tasks/waiting).
200209-15:50:35,195 nipype.workflow DEBUG:
	 Tasks currently running: 1. Pending: 1.
200209-15:50:35,197 nipype.workflow INFO:
	 [MultiProc] Running 1 tasks, and 0 jobs ready. Free memory (GB): 28.60/28.80, Free processors: 3/4.
                     Currently running:
                       * qt1proc_flow.datasink
200209-15:50:35,197 nipype.workflow INFO:
	 [Node] Setting-up "qt1proc_flow.datasink" in "/Volumes/group/proc/TIGERanalysis/qT1/workflow/qt1proc_flow/_subject_id_097-T3/datasink".
200209-15:50:35,483 nipype.workflow DEBUG:
	 [Node] Hashes: [('_outputs', [('1_check_alignment', ('/Volumes/group/proc/TIGERanalysis/qT1/workflow/qt1proc_flo

In [18]:
#SelectFiles
template2 = dict(qt1r=data_dir+'/1_check_alignment/_subject_id_{subject_id}/registered_qT1.nii.gz',
               unc_maskL = fpath+'/{subject_id}/Left_Uncinate.nii.gz',
               unc_maskR = fpath+'/{subject_id}/Right_Uncinate.nii.gz',
               cc_maskL = fpath+'/{subject_id}/Left_Cingulum_Cingulate.nii.gz',
               cc_maskR = fpath+'/{subject_id}/Right_Cingulum_Cingulate.nii.gz')

# 
#             bval=fpath+'/{subject_id}/dti.bval',
#             bvec=fpath+'/{subject_id}/dti.bvec'

sf2 = Node(SelectFiles(template2, 
                      base_directory = fpath),
          name = 'sf2')

In [19]:
get_stats=Workflow(name='get_stats')
get_stats.connect([(infosource, sf2, [('subject_id','subject_id')]),
                   (sf2, get_voxLUF, [('qt1r', 'in_file')]),
                   (sf2, get_voxLUF, [('unc_maskL', 'mask')]),
                   (get_voxLUF, datasink, [('out_file', '2_Extracted_Stats')]),
                   (sf2, get_voxLCC, [('qt1r', 'in_file')]),
                   (sf2, get_voxLCC, [('cc_maskL', 'mask')]),
                   (get_voxLCC, datasink, [('out_file', '2_Extracted_Stats.@par')]),
                   (sf2, get_voxRUF, [('qt1r', 'in_file')]),
                   (sf2, get_voxRUF, [('unc_maskR', 'mask')]),
                   (get_voxRUF, datasink, [('out_file', '2_Extracted_Stats.@par.@par')]),
                   (sf2, get_voxRCC, [('qt1r', 'in_file')]),
                   (sf2, get_voxRCC, [('cc_maskR', 'mask')]),
                   (get_voxRCC, datasink, [('out_file', '2_Extracted_Stats.@par.@par.@par')])
                  ])
get_stats.base_dir = workflow_dir
get_stats.write_graph(graph2use = 'flat')
preproc = get_stats.run('MultiProc', plugin_args={'n_procs': 4})

200209-16:22:21,425 nipype.workflow DEBUG:
	 (get_stats.infosource, get_stats.sf2): No edge data
200209-16:22:21,426 nipype.workflow DEBUG:
	 (get_stats.infosource, get_stats.sf2): new edge data: {'connect': [('subject_id', 'subject_id')]}
200209-16:22:21,427 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): No edge data
200209-16:22:21,427 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): new edge data: {'connect': [('qt1r', 'in_file')]}
200209-16:22:21,428 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): Edge data exists: {'connect': [('qt1r', 'in_file')]}
200209-16:22:21,428 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): new edge data: {'connect': [('qt1r', 'in_file'), ('unc_maskL', 'mask')]}
200209-16:22:21,429 nipype.workflow DEBUG:
	 (get_stats.get_voxLUF, get_stats.datasink): No edge data
200209-16:22:21,430 nipype.workflow DEBUG:
	 (get_stats.get_voxLUF, get_stats.datasink): new edge data: {'connect': [('out_file', '2_

200209-16:22:30,307 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_105-T1
200209-16:22:30,309 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 106-T1
200209-16:22:30,310 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_106-T1
200209-16:22:30,313 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 107-T1
200209-16:22:30,314 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_107-T1
200209-16:22:30,316 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 108-T1
200209-16:22:30,317 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_108-T1
200209-16:22:30,321 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 109-T1
200209-16:22:30,322 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_109-T1
200209-16:22:30,325 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 109-T3
200209-16:22:30,325 nipype.workflow DEBUG:
	 Param

200209-16:22:30,467 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 215-T3
200209-16:22:30,468 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_215-T3
200209-16:22:30,470 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 22-T1
200209-16:22:30,471 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_22-T1
200209-16:22:30,473 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 23-T1
200209-16:22:30,474 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_23-T1
200209-16:22:30,476 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 24-T1
200209-16:22:30,476 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_24-T1
200209-16:22:30,479 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 28-T2
200209-16:22:30,479 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_28-T2
200209-16:22:30,482 nipype.workflow DEBUG:
	 [Node] infoso

200209-16:22:30,596 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,596 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 42-T1
200209-16:22:30,597 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,597 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 41-T1
200209-16:22:30,597 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,598 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 40-T1
200209-16:22:30,598 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,599 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 39-T1
200209-16:22:30,599 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,600 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 38-T1
20020

200209-16:22:30,631 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 124-T3
200209-16:22:30,631 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,632 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 124-T1
200209-16:22:30,632 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,632 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 123-T1
200209-16:22:30,633 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,633 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 120-T1
200209-16:22:30,633 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
200209-16:22:30,634 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 12-T1
200209-16:22:30,634 nipype.workflow DEBUG:
	 Removed the identity node get_stats.infosource from the graph.
2

...

	 Linking File: /Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_06-T1/ROI_voxel-contrasts_RightCC.txt->/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_06-T1/get_voxRCC/ROI_voxel-contrasts_RightCC.txt
200209-17:00:43,936 nipype.workflow DEBUG:
	 No resources available
200209-17:00:44,462 nipype.utils DEBUG:
	 Copying File: /Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_06-T1/ROI_voxel-contrasts_RightCC.txt->/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_06-T1/get_voxRCC/ROI_voxel-contrasts_RightCC.txt
200209-17:00:45,941 nipype.workflow DEBUG:
	 No resources available
200209-17:00:46,419 nipype.utils DEBUG:
	 /Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_06-T1/ROI_voxel-contrasts_RightCC.txt
200209-17:00:47,656 nipype.utils DEBUG:
	 File: /Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_06-T1/ROI_voxel-contrasts_RightCC.txt already exists,f646f

200209-17:01:34,36 nipype.workflow DEBUG:
	 Tasks currently running: 1. Pending: 1.
200209-17:01:34,38 nipype.workflow INFO:
	 [MultiProc] Running 1 tasks, and 3 jobs ready. Free memory (GB): 28.60/28.80, Free processors: 3/4.
                     Currently running:
                       * get_stats.get_voxRUF
200209-17:01:34,72 nipype.workflow DEBUG:
	 Allocating get_stats.get_voxRUF ID=500 (0.20GB, 1 threads). Free: 28.40GB, 2 threads.
200209-17:01:34,73 nipype.workflow DEBUG:
	 Setting node inputs
200209-17:01:34,74 nipype.workflow DEBUG:
	 input: in_file
200209-17:01:34,74 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/sf2/result_sf2.pklz
200209-17:01:34,75 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/sf2/result_sf2.pklz
200209-17:01:34,124 nipype.workflow DEBUG:
	 Aggregate: False
200209-17:01:34,540 nipype.workflow DEBUG:
	 output: qt1r
200209-17:01



200209-17:01:39,434 nipype.utils DEBUG:
	 Creating directory /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF200209-17:01:39,461 nipype.workflow DEBUG:
	 Allocating get_stats.datasink ID=497 (0.20GB, 1 threads). Free: 28.00GB, 0 threads.
200209-17:01:39,426 nipype.workflow DEBUG:
	 [Node] Directory not found "/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF".
200209-17:01:39,461 nipype.workflow DEBUG:
	 Setting node inputs
200209-17:01:39,430 nipype.utils DEBUG:
	 Removing contents of /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF
200209-17:01:39,462 nipype.workflow DEBUG:
	 input: 2_Extracted_Stats
200209-17:01:39,463 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_021-T3/get_voxLUF/result_get_voxLUF.pklz
200209-17:01:39,464 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_sta

	 Needed files: /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF/ROI_voxel-contrasts_LeftUncinate.txt;/Volumes/group/proc/TIGERanalysis/qT1/data/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz;/Volumes/group/proc/TIGERanalysis/qT1/subjDir/02-T2/Left_Uncinate.nii.gz;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF/_0xf6776d83e4abc07a1fa9546beeb3dc5b_unfinished.json;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF/command.txt;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF/_inputs.pklz;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF/_node.pklz
200209-17:02:10,806 nipype.workflow DEBUG:
	 Needed dirs: /Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_02-T2/get_voxLUF/_report
200209-17:02:10,811 nipype.workflow DEBUG:
	 Removing files: 
200209-17:02:11,174 nipype.interface DEBU

	 /Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_02-T2/ROI_voxel-contrasts_LeftCC.txt
200209-17:02:37,36 nipype.workflow DEBUG:
	 Needed files: /Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_021-T3/ROI_voxel-contrasts_LeftUncinate.txt;/Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_021-T3/ROI_voxel-contrasts_LeftCC.txt;/Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_021-T3/ROI_voxel-contrasts_RightUncinate.txt;/Volumes/group/proc/TIGERanalysis/qT1/data/2_Extracted_Stats/_subject_id_021-T3/ROI_voxel-contrasts_RightCC.txt;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_021-T3/get_voxLUF/ROI_voxel-contrasts_LeftUncinate.txt;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_021-T3/get_voxLCC/ROI_voxel-contrasts_LeftCC.txt;/Volumes/group/proc/TIGERanalysis/qT1/workflow/get_stats/_subject_id_021-T3/get_voxRUF/ROI_voxel-contrasts_RightUncinate.txt;/Volu

In [ ]:
#SelectFiles
template3 = dict(qt1r = data_dir+'/1_check_alignment/_subject_id_{subject_id}/T1_acpc_bet.nii.gz',
                aseg = home + '/TIGER_FreeSurfer/TIGER_FS_subjDir/08-T2/mri')


sf3 = Node(SelectFiles(template3, 
                      base_directory = fpath),
          name = 'sf3')

In [ ]:
hippdata_flow = Workflow(name='hippdata_flow')
hippdata_flow.connect([(infosource, sf, [('subject_id', 'subject_id')]),
                      (sf, stripT1, [('t1', 'in_file')]),
                      (sf, reorient, [('qt1', 'in_file')]),
                      (reorient, datasink, [
                       ('out_file', '1_check_alignment.@par')]),
                      (reorient, register_qt1, [('out_file', 'in_file')]),
                      (stripT1, register_qt1, [('out_file', 'reference')]),
                      (register_qt1, datasink, [
                       ('out_file', '1_check_alignment.@par.@par')]),
                       (sf2, get_voxLCC, [('qt1r', 'in_file')]),
                       (sf2, get_voxLCC, [('cc_maskL', 'mask')]),
                       (get_voxLCC, datasink, [('out_file', '2_Extracted_Stats.@par')]),
                      ])

hippdata_flow.base_dir = workflow_dir
hippdata_flow.write_graph(graph2use='flat')
preproc = hippdata_flow.run('MultiProc', plugin_args={'n_procs': 4})